In [1]:
#import the file from the web
import requests
from bs4 import BeautifulSoup
import pandas as pd
from unicodedata import normalize
import re
from datetime import datetime


# I can give a number or use None to remove maximum ceiling & display all columns
pd.options.display.max_columns = None

# I want to be able to see the entire narrative, so remove the maximum width for each column
pd.options.display.max_colwidth = None


In [2]:
df=pd.read_csv("sunshine_links.csv")

In [3]:
df.head()

Unnamed: 0    key_0      Country     City    Jan    Feb    Mar    Apr  \
0           0   Gagnoa  Ivory Coast   Gagnoa  183.0  180.0  196.0  188.0   
1           1   Bouaké  Ivory Coast   Bouaké  242.0  224.0  219.0  194.0   
2           2  Abidjan  Ivory Coast  Abidjan  223.0  223.0  239.0  214.0   
3           3  Odienné  Ivory Coast  Odienné  242.0  220.2  217.3  214.7   
4           4    Ferké  Ivory Coast    Ferké  279.0  249.0  253.0  229.0   

     May    Jun    Jul    Aug    Sep    Oct    Nov    Dec    Year Ref.  \
0  181.0  118.0   97.0   80.0  110.0  155.0  171.0  164.0  1823.0  [2]   
1  208.0  145.0  104.0   82.0  115.0  170.0  191.0  198.0  2092.0  [2]   
2  205.0  128.0  137.0  125.0  139.0  215.0  224.0  224.0  2296.0  [2]   
3  248.8  221.8  183.5  174.5  185.4  235.8  252.0  242.6  2638.6  [3]   
4  251.0  221.0  183.0  151.0  173.0  245.0  261.0  262.0  2757.0  [2]   

  Continent  country_url        city_url naming_country naming_city  \
0    Africa  ivory-coast          gagnoa    Ivory Coast      Gagnoa   
1    Africa  ivory-coast          bouaké    Ivory Coast      Bouaké   
2    Africa  ivory-coast         abidjan    Ivory Coast     Abidjan   
3    Africa  ivory-coast         odienné    Ivory Coast     Odienné   
4    Africa  ivory-coast  ferkessédougou    Ivory Coast       Ferké   

   sun_country        sun_city  \
0  Ivory Coast          Gagnoa   
1  Ivory Coast          Bouaké   
2  Ivory Coast         Abidjan   
3  Ivory Coast         Odienné   
4  Ivory Coast  Ferkessédougou   

                                                                         dec_url_city  \
0          https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
1          https://www.sunrise-and-sunset.com/en/sun/ivory-coast/bouaké/2023/december   
2         https://www.sunrise-and-sunset.com/en/sun/ivory-coast/abidjan/2023/december   
3         https://www.sunrise-and-sunset.com/en/sun/ivory-coast/odienné/2023/december   
4  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/ferkessédougou/2023/december   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [4]:
df["year_url_city"]


0              https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/
1              https://www.sunrise-and-sunset.com/en/sun/ivory-coast/bouaké/2023/
2             https://www.sunrise-and-sunset.com/en/sun/ivory-coast/abidjan/2023/
3             https://www.sunrise-and-sunset.com/en/sun/ivory-coast/odienné/2023/
4      https://www.sunrise-and-sunset.com/en/sun/ivory-coast/ferkessédougou/2023/
                                          ...                                    
388        https://www.sunrise-and-sunset.com/en/sun/new-zealand/wellington/2023/
389          https://www.sunrise-and-sunset.com/en/sun/new-zealand/hamilton/2023/
390          https://www.sunrise-and-sunset.com/en/sun/new-zealand/auckland/2023/
391                     https://www.sunrise-and-sunset.com/en/sun/fiji/suva/2023/
392           https://www.sunrise-and-sunset.com/en/sun/new-zealand/dunedin/2023/
Name: year_url_city, Length: 393, dtype: object

In [5]:
df

Unnamed: 0       key_0      Country        City    Jan    Feb    Mar  \
0             0      Gagnoa  Ivory Coast      Gagnoa  183.0  180.0  196.0   
1             1      Bouaké  Ivory Coast      Bouaké  242.0  224.0  219.0   
2             2     Abidjan  Ivory Coast     Abidjan  223.0  223.0  239.0   
3             3     Odienné  Ivory Coast     Odienné  242.0  220.2  217.3   
4             4       Ferké  Ivory Coast       Ferké  279.0  249.0  253.0   
..          ...         ...          ...         ...    ...    ...    ...   
388         388  Wellington  New Zealand  Wellington  240.3  205.0  194.7   
389         389    Hamilton  New Zealand    Hamilton  229.8  192.9  193.3   
390         390    Auckland  New Zealand    Auckland  228.8  194.9  189.2   
391         391        Suva         Fiji        Suva  192.2  178.0  170.5   
392         392     Dunedin  New Zealand     Dunedin  179.6  158.0  146.1   

       Apr    May    Jun    Jul    Aug    Sep    Oct    Nov    Dec    Year  \
0    188.0  181.0  118.0   97.0   80.0  110.0  155.0  171.0  164.0  1823.0   
1    194.0  208.0  145.0  104.0   82.0  115.0  170.0  191.0  198.0  2092.0   
2    214.0  205.0  128.0  137.0  125.0  139.0  215.0  224.0  224.0  2296.0   
3    214.7  248.8  221.8  183.5  174.5  185.4  235.8  252.0  242.6  2638.6   
4    229.0  251.0  221.0  183.0  151.0  173.0  245.0  261.0  262.0  2757.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...     ...   
388  153.8  126.0  102.3  111.4  137.2  163.2  191.1  210.8  222.9  2058.7   
389  165.1  138.3  112.8  126.4  144.1  147.5  174.8  187.1  207.6  2019.6   
390  157.3  139.8  110.3  128.1  142.9  148.6  178.1  188.1  197.2  2003.1   
391  153.0  145.7  141.0  136.4  142.6  135.0  164.3  168.0  195.3  1922.0   
392  125.9  108.4   95.3  110.6  122.2  136.8  165.5  166.9  168.3  1683.7   

      Ref. Continent  country_url        city_url naming_country naming_city  \
0      [2]    Africa  ivory-coast          gagnoa    Ivory Coast      Gagnoa   
1      [2]    Africa  ivory-coast          bouaké    Ivory Coast      Bouaké   
2      [2]    Africa  ivory-coast         abidjan    Ivory Coast     Abidjan   
3      [3]    Africa  ivory-coast         odienné    Ivory Coast     Odienné   
4      [2]    Africa  ivory-coast  ferkessédougou    Ivory Coast       Ferké   
..     ...       ...          ...             ...            ...         ...   
388      ?   Oceania  new-zealand      wellington    New Zealand  Wellington   
389      ?   Oceania  new-zealand        hamilton    New Zealand    Hamilton   
390      ?   Oceania  new-zealand        auckland    New Zealand    Auckland   
391  [193]   Oceania         fiji            suva           Fiji        Suva   
392  [194]   Oceania  new-zealand         dunedin    New Zealand     Dunedin   

     sun_country        sun_city  \
0    Ivory Coast          Gagnoa   
1    Ivory Coast          Bouaké   
2    Ivory Coast         Abidjan   
3    Ivory Coast         Odienné   
4    Ivory Coast  Ferkessédougou   
..           ...             ...   
388  New Zealand      Wellington   
389  New Zealand        Hamilton   
390  New Zealand        Auckland   
391         Fiji            Suva   
392  New Zealand         Dunedin   

                                                                           dec_url_city  \
0            https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
1            https://www.sunrise-and-sunset.com/en/sun/ivory-coast/bouaké/2023/december   
2           https://www.sunrise-and-sunset.com/en/sun/ivory-coast/abidjan/2023/december   
3           https://www.sunrise-and-sunset.com/en/sun/ivory-coast/odienné/2023/december   
4    https://www.sunrise-and-sunset.com/en/sun/ivory-coast/ferkessédougou/2023/december   
..                                                                                  ...   
388      https://www.sunrise-and-sunset.com/en/sun/new-zealand/wellington/2023/december   
389        https://ww

In [6]:
df_tables=pd.read_html("https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/")

# for df_table in df_tables:
#     df_tables['tables_url']="https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/"

In [7]:
#for dec_duration by scraping

def get_year_by_city(url):
    try:
        ls_tables=pd.read_html(url)

        ls_tables_columns_standardized = []
        for df_table in ls_tables:
            df_table_copy = df_table.copy()
            df_table_copy.columns = df_table_copy.columns.get_level_values(1)
            ls_tables_columns_standardized.append(df_table_copy)

        df_all_months = pd.concat(ls_tables_columns_standardized, axis=0, ignore_index=True)
        df_all_months['all_months_url']=url
        return df_all_months
    except:
        pass

    

yearly_tables=df.year_url_city.apply(get_year_by_city)

In [8]:
len(yearly_tables)

393

In [9]:
type(yearly_tables)

pandas.core.series.Series

In [10]:
yearly_tables_twenty=df.year_url_city[0:20].apply(get_year_by_city)

In [11]:
yearly_tables_twenty

0                                             Date Sunrise Sunset Day length  \
0         1 January 2023, Sunday   06:34  18:19      11:44   
1         2 January 2023, Monday   06:35  18:20      11:44   
2        3 January 2023, Tuesday   06:35  18:20      11:44   
3      4 January 2023, Wednesday   06:36  18:21      11:44   
4       5 January 2023, Thursday   06:36  18:21      11:45   
..                           ...     ...    ...        ...   
360  27 December 2023, Wednesday   06:32  18:16      11:44   
361   28 December 2023, Thursday   06:32  18:17      11:44   
362     29 December 2023, Friday   06:33  18:17      11:44   
363   30 December 2023, Saturday   06:33  18:18      11:44   
364     31 December 2023, Sunday   06:34  18:18      11:44   

                                                         all_months_url  
0    https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/  
1    https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/  
2    https://ww

In [12]:
ls_yearly_tables=[]
for yearly_table in yearly_tables:
    if yearly_table is not None:
        ls_yearly_tables.append(yearly_table) 

In [16]:
df_yearly_tables=pd.concat(ls_yearly_tables)

In [ ]:
df_yearly_tables.to_csv("yearly_table.csv")

In [20]:
df=df.drop(columns='key_0')

In [21]:
df_sunshine_year = pd.merge(df, df_yearly_tables, left_on=df.year_url_city, right_on=df_yearly_tables.all_months_url, how='left')
df_sunshine_year.head()

key_0  \
0  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/   
1  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/   
2  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/   
3  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/   
4  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/   

   Unnamed: 0      Country    City    Jan    Feb    Mar    Apr    May    Jun  \
0           0  Ivory Coast  Gagnoa  183.0  180.0  196.0  188.0  181.0  118.0   
1           0  Ivory Coast  Gagnoa  183.0  180.0  196.0  188.0  181.0  118.0   
2           0  Ivory Coast  Gagnoa  183.0  180.0  196.0  188.0  181.0  118.0   
3           0  Ivory Coast  Gagnoa  183.0  180.0  196.0  188.0  181.0  118.0   
4           0  Ivory Coast  Gagnoa  183.0  180.0  196.0  188.0  181.0  118.0   

    Jul   Aug    Sep    Oct    Nov    Dec    Year Ref. Continent  country_url  \
0  97.0  80.0  110.0  155.0  171.0  164.0  1823.0  [2]    Africa  ivory-coast   
1  97.0  80.0  110.0  155.0  171.0  164.0  1823.0  [2]    Africa  ivory-coast   
2  97.0  80.0  110.0  155.0  171.0  164.0  1823.0  [2]    Africa  ivory-coast   
3  97.0  80.0  110.0  155.0  171.0  164.0  1823.0  [2]    Africa  ivory-coast   
4  97.0  80.0  110.0  155.0  171.0  164.0  1823.0  [2]    Africa  ivory-coast   

  city_url naming_country naming_city  sun_country sun_city  \
0   gagnoa    Ivory Coast      Gagnoa  Ivory Coast   Gagnoa   
1   gagnoa    Ivory Coast      Gagnoa  Ivory Coast   Gagnoa   
2   gagnoa    Ivory Coast      Gagnoa  Ivory Coast   Gagnoa   
3   gagnoa    Ivory Coast      Gagnoa  Ivory Coast   Gagnoa   
4   gagnoa    Ivory Coast      Gagnoa  Ivory Coast   Gagnoa   

                                                                 dec_url_city  \
0  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
1  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
2  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
3  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   
4  https://www.sunrise-and-sunset.com/en/sun/ivory-coast/gagnoa/2023/december   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

In [22]:
df_sunshine_year.shape

(108869, 42)

In [23]:
df_sunshine_year.to_csv("sunshine_year.csv")